This Notebook is a Stable-diffusion tool which allows you to find similiar tokens from the SD 1.5 vocab.json that you can use for text-to-image generation. Try this Free online SD 1.5 generator with the results: https://perchance.org/fusion-ai-image-generator

Scroll to the bottom of the notebook to see the guide for how this works.

In [ ]:
# @title ✳️ Load/initialize values
# Load the tokens into the colab
!git clone https://huggingface.co/datasets/codeShare/sd_tokens
import torch
from torch import linalg as LA
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
%cd /content/sd_tokens
token = torch.load('sd15_tensors.pt', map_location=device, weights_only=True)
#-----#
VOCAB_FILENAME = 'tokens_most_similiar_to_girl'
ACTIVE_IMG = ''
#-----#

# Define functions/constants
NUM_TOKENS = 49407
NUM_PREFIX = 13662
NUM_SUFFIX = 32901

loaded_Image_A = False

#Import the vocab.json
import json
import pandas as pd

# Read suffix.json
with open('suffix.json', 'r') as f:
    data = json.load(f)
_df = pd.DataFrame({'count': data})['count']
suffix = {
    key : value for key, value in _df.items()
}
# Read prefix json
with open('prefix.json', 'r') as f:
    data = json.load(f)
_df = pd.DataFrame({'count': data})['count']
prefix = {
    key : value for key, value in _df.items()
}

# Read to_suffix.json
with open('to_suffix.json', 'r') as f:
    data = json.load(f)
_df = pd.DataFrame({'count': data})['count']
suffix_to_vocab = {
    key : value for key, value in _df.items()
}

# Read to_prefix.json
with open('to_prefix.json', 'r') as f:
    data = json.load(f)
_df = pd.DataFrame({'count': data})['count']
prefix_to_vocab = {
    key : value for key, value in _df.items()
}

#-----#


# Read to_suffix.json (reversing key and value)
with open('to_suffix.json', 'r') as f:
    data = json.load(f)
_df = pd.DataFrame({'count': data})['count']
vocab_to_suffix = {
    value : key for key, value in _df.items()
}

# Read to_prefix.json (reversing key and value)
with open('to_prefix.json', 'r') as f:
    data = json.load(f)
_df = pd.DataFrame({'count': data})['count']
vocab_to_prefix = {
    value : key for key, value in _df.items()
}


#-----#

#get token from id (excluding tokens with special symbols)
def vocab(id):
  _id = f'{id}'
  if _id in vocab_to_suffix:
    _id = vocab_to_suffix[_id]
    return suffix[_id]
  if _id in vocab_to_prefix:
    _id = vocab_to_prefix[_id]
    return prefix[_id]
  return ' ' #<---- return whitespace if other id like emojis etc.
#--------#

#print(get_token(35894))


In [ ]:
# @title ⚡ Get similiar tokens
import torch
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)

# @markdown Write name of token to match against
token_name = " banana" # @param {type:'string',"placeholder":"leave empty for random value token"}

prompt = token_name
# @markdown (optional) Mix the token with something else
mix_with = "" # @param {"type":"string","placeholder":"leave empty for random value token"}
mix_method = "None" # @param ["None" , "Average", "Subtract"] {allow-input: true}
w = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}
# @markdown Limit char size of included token

min_char_size = 0 # param {type:"slider", min:0, max: 50, step:1}
char_range = 50 # param {type:"slider", min:0, max: 50, step:1}

tokenizer_output = tokenizer(text = prompt)
input_ids = tokenizer_output['input_ids']
id_A = input_ids[1]
A = torch.tensor(token[id_A])
A = A/A.norm(p=2, dim=-1, keepdim=True)
#-----#
tokenizer_output = tokenizer(text = mix_with)
input_ids = tokenizer_output['input_ids']
id_C = input_ids[1]
C = torch.tensor(token[id_C])
C = C/C.norm(p=2, dim=-1, keepdim=True)
#-----#
sim_AC = torch.dot(A,C)
#-----#
print(input_ids)
#-----#

#if no imput exists we just randomize the entire thing
if (prompt == ""):
  id_A = -1
  print("Tokenized prompt tensor A is a random valued tensor with no ID")
  R = torch.rand(A.shape)
  R = R/R.norm(p=2, dim=-1, keepdim=True)
  A = R
  name_A = 'random_A'

#if no imput exists we just randomize the entire thing
if (mix_with == ""):
  id_C = -1
  print("Tokenized prompt  'mix_with' tensor C is a random valued tensor with no ID")
  R = torch.rand(A.shape)
  R = R/R.norm(p=2, dim=-1, keepdim=True)
  C = R
  name_C = 'random_C'

name_A = "A of random type"
if (id_A>-1):
  name_A = vocab(id_A)

name_C = "token C of random type"
if (id_C>-1):
  name_C = vocab(id_C)

print(f"The similarity between A '{name_A}' and C '{name_C}' is {round(sim_AC.item()*100,2)} %")

if (mix_method ==  "None"):
  print("No operation")

if (mix_method ==  "Average"):
  A = w*A + (1-w)*C
  _A = LA.vector_norm(A, ord=2)
  print(f"Tokenized prompt tensor A '{name_A}' token has been recalculated as A = w*A + (1-w)*C , where C is '{name_C}' token , for w = {w}  ")

if (mix_method ==  "Subtract"):
  tmp =  w*A - (1-w)*C
  tmp = tmp/tmp.norm(p=2, dim=-1, keepdim=True)
  A = tmp
  #//---//
  print(f"Tokenized prompt tensor A '{name_A}' token has been recalculated as A = _A*norm(w*A  - (1-w)*C) , where C is '{name_C}' token , for w = {w} ")

#OPTIONAL : Add/subtract + normalize above result with another token. Leave field empty to get a random value tensor

dots = torch.zeros(NUM_TOKENS)
for index in range(NUM_TOKENS):
  id_B = index
  B = torch.tensor(token[id_B])
  B = B/B.norm(p=2, dim=-1, keepdim=True)
  sim_AB = torch.dot(A,B)
  dots[index] = sim_AB


sorted, indices = torch.sort(dots,dim=0 , descending=True)
#----#
if (mix_method ==  "Average"):
  print(f'Calculated all cosine-similarities between the average of token {name_A} and {name_C} with Id_A = {id_A} and mixed Id_C = {id_C} as a 1x{sorted.shape[0]} tensor')
if (mix_method ==  "Subtract"):
  print(f'Calculated all cosine-similarities between the subtract of token {name_A} and {name_C} with Id_A = {id_A} and mixed Id_C = {id_C} as a 1x{sorted.shape[0]} tensor')
if (mix_method ==  "None"):
  print(f'Calculated all cosine-similarities between the token {name_A} with Id_A = {id_A} with the the rest of the {NUM_TOKENS} tokens as a 1x{sorted.shape[0]} tensor')

#Produce a list id IDs that are most similiar to the prompt ID at positiion 1 based on above result

# @markdown Set print options
list_size = 100 # @param {type:'number'}
print_ID = False # @param {type:"boolean"}
print_Similarity = True # @param {type:"boolean"}
print_Name = True # @param {type:"boolean"}
print_Divider = True # @param {type:"boolean"}


if (print_Divider):
  print('//---//')

print('')
print('Here is the result : ')
print('')

for index in range(list_size):
  id = indices[index].item()
  if (print_Name):
    print(f'{vocab(id)}') # vocab item
  if (print_ID):
    print(f'ID = {id}') # IDs
  if (print_Similarity):
    print(f'similiarity = {round(sorted[index].item()*100,2)} %')
  if (print_Divider):
    print('--------')

#Print the sorted list from above result

#The prompt will be enclosed with the <|start-of-text|> and <|end-of-text|> tokens, which is why output will be [49406, ... , 49407].

#You can leave the 'prompt' field empty to get a random value tensor. Since the tensor is random value, it will not correspond to any tensor in the vocab.json list , and this it will have no ID.

# Save results as .db file
import shelve
VOCAB_FILENAME = 'tokens_most_similiar_to_' + name_A.replace('</w>','').strip()
d = shelve.open(VOCAB_FILENAME)
#NUM TOKENS == 49407
for index in range(NUM_TOKENS):
  #print(d[f'{index}']) #<-----Use this to read values from the .db file
  d[f'{index}']= vocab(indices[index].item()) #<---- write values to .db file
#----#
d.close() #close the file
# See this link for additional stuff to do with shelve: https://docs.python.org/3/library/shelve.html

Below image interrogator appends CLIP tokens to either end of the 'must_contain' text , and seeks to maximize similarity with the image encoding.

It takes a long while to check all the tokens (too long!) so this cell only samples a range of the 49K available tokens.

You can run this cell, then paste the result into the 'must_contain' box , and then run the cell again.

Check the sd_tokens folder for stored .db files from running the '⚡ Get similiar tokens' cell. These can be used in the ⚡+🖼️ -> 📝 Token-Sampling Image interrogator cell


In [ ]:
# @title 🖼️ Upload an image
from google.colab import files
def upload_files():
  from google.colab import files
  uploaded = files.upload()
  for k, v in uploaded.items():
    open(k, 'wb').write(v)
  return list(uploaded.keys())
#Get image
# You can use "http://images.cocodataset.org/val2017/000000039769.jpg" for testing
image_url = "" # @param {"type":"string","placeholder":"leave empty for local upload (scroll down to see it)"}
colab_image_path = "" # @param {"type":"string","placeholder": "eval. as '/content/sd_tokens/' + **your input**"}
# @markdown --------------------------

image_path = ""

from PIL import Image
import requests
image_A = ""
#----#
if image_url == "":
  import cv2
  from google.colab.patches import cv2_imshow
  # Open the image.
  if colab_image_path == "":
    keys =  upload_files()
    for key in keys:
      image_A = cv2.imread("/content/sd_tokens/" + key)
      colab_image_path = "/content/sd_tokens/" + key
      image_path = "/content/sd_tokens/" + key
  else:
    image_A = cv2.imread("/content/sd_tokens/" + colab_image_path)
else:
  image_A = Image.open(requests.get(image_url, stream=True).raw)
#------#



In [ ]:
# @title ⚡+🖼️ -> 📝 Token-Sampling Image interrogator
#-----#
NUM_TOKENS = 49407
import shelve
db_vocab = shelve.open(VOCAB_FILENAME)
print(f'using the tokens found in {VOCAB_FILENAME}.db as the vocab')
# @markdown # What do you want to to mimic?
use = '🖼️image_encoding from image' # @param ['📝text_encoding from prompt', '🖼️image_encoding from image']
# @markdown --------------------------
use_token_padding = True # param {type:"boolean"} <---- Enabled by default
prompt = "photo of a banana" # @param {"type":"string","placeholder":"Write a prompt"}
#-----#
prompt_A = prompt
if(image_path != "") : image_A = cv2.imread("/content/sd_tokens/" + image_path)
#-----#

from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
#-----#
if(use == '🖼️image_encoding from image'):
  # Get image features
  inputs = processor(images=image_A, return_tensors="pt")
  image_features = model.get_image_features(**inputs)
  image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)
  name_A = "the image"
#-----#
if(use == '📝text_encoding from prompt'):
  # Get text features
  inputs = tokenizer(text = prompt, padding=True, return_tensors="pt")
  text_features_A = model.get_text_features(**inputs)
  name_A = prompt
#-----#
# @markdown # The output...
must_start_with = "" # @param {"type":"string","placeholder":"write a text"}
must_contain = "" # @param {"type":"string","placeholder":"write a text"}
must_end_with = "" # @param {"type":"string","placeholder":"write a text"}
# @markdown -----
# @markdown # Use a range of tokens from the vocab.json (slow method)
start_search_at_index = 0 # @param {type:"slider", min:0, max: 49407, step:100}
# @markdown The lower the start_index, the more similiar the sampled tokens will be to the target token assigned in the '⚡ Get similiar tokens' cell". If the cell was not run, then it will use tokens ordered by similarity to the "girl\</w>" token
start_search_at_ID = start_search_at_index
search_range = 1000 # @param {type:"slider", min:100, max:49407, step:100}

samples_per_iter = 10 # @param {type:"slider", min:10, max: 100, step:10}

iterations = 5 # @param {type:"slider", min:1, max: 20, step:0}
restrictions = 'None' # @param ["None", "Suffix only", "Prefix only"]
#markdown Limit char size of included token <----- Disabled
min_char_size = 0 #param {type:"slider", min:0, max: 20, step:1}
char_range = 50 #param {type:"slider", min:0, max: 20, step:1}
# markdown # ...or paste prompt items
# markdown Format must be {item1|item2|...}. You can aquire prompt items using the Randomizer in the fusion gen: https://perchance.org/fusion-ai-image-generator
_enable = False # param {"type":"boolean"}
prompt_items = "" # param {"type":"string","placeholder":"{item1|item2|...}"}
#-----#
#-----#
START = start_search_at_ID
RANGE =  min(search_range , max(1,NUM_TOKENS - start_search_at_ID))
#-----#
import math, random
NUM_PERMUTATIONS = 6
ITERS = iterations
#-----#
#LOOP START
#-----#
# Check if original solution is best
best_sim = 0
name = must_start_with + must_contain + must_end_with
ids = processor.tokenizer(text=name, padding=use_token_padding, return_tensors="pt")
text_features = model.get_text_features(**ids)
text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
#------#
sim = 0
if(use == '🖼️image_encoding from image'):
  logit_scale = model.logit_scale.exp()
  torch.matmul(text_features, image_features.t()) * logit_scale
  sim = torch.nn.functional.cosine_similarity(text_features, image_features) * logit_scale
#-----#
if(use == '📝text_encoding from prompt'):
  sim = torch.nn.functional.cosine_similarity(text_features, text_features_A)
#-----#
best_sim = sim
best_name = name
name_B = must_contain
#------#
results_sim = torch.zeros(ITERS*NUM_PERMUTATIONS)
results_name_B = {}
results_name = {}
#-----#
for iter in range(ITERS):
  dots = torch.zeros(min(list_size,RANGE))
  is_trail = torch.zeros(min(list_size,RANGE))

  #-----#

  for index in range(samples_per_iter):
    _start = START
    id_C = random.randint(_start , _start + RANGE)
    name_C = db_vocab[f'{id_C}']
    is_Prefix = 0
    #Skip if non-AZ characters are found
    #???
    #-----#
    # Decide if we should process prefix/suffix tokens
    if name_C.find('</w>')<=-1:
      is_Prefix = 1
      if restrictions != "Prefix only":
        continue
    else:
      if restrictions == "Prefix only":
        continue
    #-----#
    # Decide if char-size is within range
    if len(name_C) < min_char_size:
      continue
    if len(name_C) > min_char_size + char_range:
      continue
    #-----#
    name_CB = must_start_with + name_C + name_B + must_end_with
    if is_Prefix>0:
      name_CB = must_start_with + ' ' + name_C + '-' + name_B + ' ' + must_end_with
    #-----#
    if(use == '🖼️image_encoding from image'):
      ids_CB = processor.tokenizer(text=name_CB, padding=use_token_padding, return_tensors="pt")
      text_features = model.get_text_features(**ids_CB)
      text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
      logit_scale = model.logit_scale.exp()
      torch.matmul(text_features, image_features.t()) * logit_scale
      sim_CB = torch.nn.functional.cosine_similarity(text_features, image_features) * logit_scale
    #-----#
    if(use == '📝text_encoding from prompt'):
      ids_CB = processor.tokenizer(text=name_CB, padding=use_token_padding, return_tensors="pt")
      text_features = model.get_text_features(**ids_CB)
      text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
      sim_CB = torch.nn.functional.cosine_similarity(text_features, text_features_A)
    #-----#
    #-----#
    if restrictions == "Prefix only":
      result = sim_CB
      result = result.item()
      dots[index] = result
      continue
    #-----#
    if(use == '🖼️image_encoding from image'):
      name_BC = must_start_with + name_B + name_C + must_end_with
      ids_BC = processor.tokenizer(text=name_BC, padding=use_token_padding, return_tensors="pt")
      text_features = model.get_text_features(**ids_BC)
      text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
      logit_scale = model.logit_scale.exp()
      torch.matmul(text_features, image_features.t()) * logit_scale
      sim_BC = torch.nn.functional.cosine_similarity(text_features, image_features) * logit_scale
    #-----#
    if(use == '📝text_encoding from prompt'):
      name_BC = must_start_with + name_B + name_C + must_end_with
      ids_BC = processor.tokenizer(text=name_BC, padding=use_token_padding, return_tensors="pt")
      text_features = model.get_text_features(**ids_BC)
      text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
      sim_BC = torch.nn.functional.cosine_similarity(text_features, text_features_A)
    #-----#
    result = sim_CB
    if(sim_BC > sim_CB):
      is_trail[index] = 1
      result = sim_BC
    #-----#
    #result = absolute_value(result.item())
    result = result.item()
    dots[index] = result
  #----#
  sorted, indices = torch.sort(dots,dim=0 , descending=True)
  # @markdown ----------
  # @markdown # Print options
  list_size = 100 # param {type:'number'}
  print_ID = False # @param {type:"boolean"}
  print_Similarity = True # @param {type:"boolean"}
  print_Name = True # @param {type:"boolean"}
  print_Divider = True # @param {type:"boolean"}
  print_Suggestions = False # @param {type:"boolean"}
  #----#
  if (print_Divider):
    print('//---//')
  #----#
  print('')

  used_reference = f'the text_encoding for {prompt_A}'
  if(use == '🖼️image_encoding from image'):
    used_reference = 'the image input'
  print(f'These token pairings within the range ID = {_start} to ID = {_start + RANGE} most closely match {used_reference}: ')
  print('')
  #----#
  aheads = "{"
  trails = "{"
  tmp = ""
  #----#
  max_sim_ahead = 0
  max_sim_trail = 0
  sim = 0
  max_name_ahead = ''
  max_name_trail = ''
  #----#
  for index in range(min(list_size,RANGE)):
    id = _start + indices[index].item()
    name = db_vocab[f'{id}']
    #-----#
    if (name.find('</w>')<=-1):
      name = name + '-'
    if(is_trail[index]>0):
      trails = trails + name + "|"
    else:
      aheads = aheads + name + "|"
    #----#
    sim = sorted[index].item()
    #----#
    if(is_trail[index]>0):
      if sim>max_sim_trail:
        max_sim_trail = sim
        max_name_trail = name
        max_name_trail = max_name_trail.strip()

    else:
      if sim>max_sim_ahead:
        max_sim_ahead = sim
        max_name_ahead = name
  #------#
  trails = (trails + "&&&&").replace("|&&&&", "}").replace("</w>", " ").replace("{&&&&", "")
  aheads = (aheads + "&&&&").replace("|&&&&", "}").replace("</w>", " ").replace("{&&&&", "")
  #-----#

  if(print_Suggestions):
    print(f"place these items ahead of prompt :  {aheads}")
    print("")
    print(f"place these items behind the prompt : {trails}")
    print("")

  tmp = must_start_with + ' ' + max_name_ahead + name_B + ' ' + must_end_with
  tmp = tmp.strip().replace('</w>', ' ')
  print(f"max_similarity_ahead = {round(max_sim_ahead,2)} % when using '{tmp}' ")
  print("")
  tmp = must_start_with + ' ' + name_B + max_name_trail + ' ' + must_end_with
  tmp = tmp.strip().replace('</w>', ' ')
  print(f"max_similarity_trail = {round(max_sim_trail,2)} % when using '{tmp}' ")
  #-----#
  #STEP 2
  import random
  #-----#
  for index in range(NUM_PERMUTATIONS):
    name_inner = ''
    if index == 0 : name_inner = name_B
    if index == 1: name_inner = max_name_ahead
    if index == 2: name_inner = max_name_trail
    if index == 3: name_inner = name_B + max_name_trail
    if index == 4: name_inner = max_name_ahead + name_B
    if index == 5: name_inner = max_name_ahead + name_B + max_name_trail
    if name_inner == '': name_inner = max_name_ahead + name_B + max_name_trail

    name = must_start_with  + name_inner + must_end_with
    #----#
    ids = processor.tokenizer(text=name, padding=use_token_padding, return_tensors="pt")
    #----#
    sim = 0
    if(use == '🖼️image_encoding from image'):
      text_features = model.get_text_features(**ids)
      text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
      logit_scale = model.logit_scale.exp()
      torch.matmul(text_features, image_features.t()) * logit_scale
      sim = torch.nn.functional.cosine_similarity(text_features, image_features) * logit_scale
    #-----#
    if(use == '📝text_encoding from prompt'):
      text_features = model.get_text_features(**ids)
      text_features = text_features / text_features.norm(p=2, dim=-1, keepdim=True)
      sim = torch.nn.functional.cosine_similarity(text_features, text_features_A)
    #-----#
    results_name[iter*NUM_PERMUTATIONS + index] = name
    results_sim[iter*NUM_PERMUTATIONS + index] = sim
    results_name_B[iter*NUM_PERMUTATIONS + index] = name_inner.replace('</w>',' ')
  #------#
  #name_B  = results_name_B[iter*NUM_PERMUTATIONS + random.randint(0,3)]
  tmp = iter*NUM_PERMUTATIONS
  _name_B=''
  if results_sim[tmp+1]>results_sim[tmp+2]: _name_B = results_name_B[tmp + 3]
  if results_sim[tmp+2]>results_sim[tmp+1]: _name_B = results_name_B[tmp + 4]

  if _name_B != name_B:
    name_B=_name_B
  else:
    name_B = results_name_B[tmp + 5]

#--------#
print('')
if(use == '🖼️image_encoding from image'  and colab_image_path != ""):
  from google.colab.patches import cv2_imshow
  cv2_imshow(image_A)
#-----#
print('')
sorted, indices = torch.sort(results_sim,dim=0 , descending=True)

for index in range(ITERS*NUM_PERMUTATIONS):
  name_inner = results_name[indices[index].item()]
  print(must_start_with  + name_inner + must_end_with)
  print(f'similiarity = {round(sorted[index].item(),2)} %')
  print('------')
#------#
db_vocab.close() #close the file

In [ ]:
# @title (Optional) ⚡Actively set which Vocab list to use for the interrogator
token_name = "" # @param {"type":"string","placeholder":"Write a token_name used earlier"}
VOCAB_FILENAME = 'tokens_most_similiar_to_' + token_name.replace('</w>','').strip()
print(f'Using a vocab ordered to most similiar to the token {token_name}')

In [ ]:
# @title 💫 Compare Text encodings
prompt_A = "banana" # @param {"type":"string","placeholder":"Write a prompt"}
prompt_B = "bike " # @param {"type":"string","placeholder":"Write a prompt"}
use_token_padding = True # param {type:"boolean"} <----- Enabled by default
#-----#
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14",
clean_up_tokenization_spaces = False)
#-----#
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
#----#
inputs = tokenizer(text = prompt_A, padding=True, return_tensors="pt")
text_features_A = model.get_text_features(**inputs)
text_features_A = text_features_A / text_features_A.norm(p=2, dim=-1, keepdim=True)
name_A = prompt_A
#----#
inputs = tokenizer(text = prompt_B, padding=True, return_tensors="pt")
text_features_B = model.get_text_features(**inputs)
text_features_B = text_features_B / text_features_B.norm(p=2, dim=-1, keepdim=True)
name_B = prompt_B
#----#
import torch
sim_AB = torch.nn.functional.cosine_similarity(text_features_A, text_features_B)
#----#
print(f'The similarity between the text_encoding for A:"{prompt_A}" and B: "{prompt_B}" is {round(sim_AB.item()*100,2)} %')

You can write an url or upload a file locally from your device to use as reference. The image will by saved in the 'sd_tokens' folder. Note that the 'sd_tokens' folder will be deleted upon exiting this runtime.



# How does this notebook work?

Similiar vectors = similiar output in the SD 1.5 / SDXL / FLUX model

CLIP converts the prompt text to vectors (“tensors”) , with float32 values usually ranging from -1 to 1.

Dimensions are \[ 1x768 ] tensors for SD 1.5 , and a \[ 1x768 , 1x1024 ] tensor for SDXL and FLUX.

The SD models and FLUX converts these vectors to an image.

This notebook takes an input string , tokenizes it and matches the first token against the 49407 token vectors in the vocab.json : [https://huggingface.co/black-forest-labs/FLUX.1-dev/tree/main/tokenizer](https://www.google.com/url?q=https%3A%2F%2Fhuggingface.co%2Fblack-forest-labs%2FFLUX.1-dev%2Ftree%2Fmain%2Ftokenizer)

It finds the “most similiar tokens” in the list. Similarity is the theta angle between the token vectors.

<div>
<img src="https://huggingface.co/datasets/codeShare/sd_tokens/resolve/main/cosine.jpeg" width="300"/>
</div>

The angle is calculated using cosine similarity , where 1 = 100% similarity (parallell vectors) , and 0 = 0% similarity (perpendicular vectors).

Negative similarity is also possible.

# How can I use it?

If you are bored of prompting “girl” and want something similiar you can run this notebook and use the “chick” token at 21.88% similarity , for example

You can also run a mixed search , like “cute+girl”/2 , where for example “kpop” has a 16.71% similarity

There are some strange tokens further down the list you go. Example: tokens similiar to the token "pewdiepie</w>" (yes this is an actual token that exists in CLIP)

<div>
<img src="https://lemmy.world/pictrs/image/a1cd284e-3341-4284-9949-5f8b58d3bd1f.jpeg" width="300"/>
</div>

Each of these correspond to a unique 1x768 token vector.

The higher the ID value , the less often the token appeared in the CLIP training data.

To reiterate; this is the CLIP model training data , not the SD-model training data.

So for certain models , tokens with high ID can give very consistent results , if the SD model is trained to handle them.

Example of this can be anime models , where japanese artist names can affect the output greatly.  

Tokens with high ID will often give the "fun" output when used in very short prompts.

# What about token vector length?

If you are wondering about token magnitude,
Prompt weights like (banana:1.2) will scale the magnitude of the corresponding 1x768 tensor(s) by 1.2 . So thats how prompt token magnitude works.

Source: [https://huggingface.co/docs/diffusers/main/en/using-diffusers/weighted\_prompts](https://www.google.com/url?q=https%3A%2F%2Fhuggingface.co%2Fdocs%2Fdiffusers%2Fmain%2Fen%2Fusing-diffusers%2Fweighted_prompts)\*

So TLDR; vector direction = “what to generate” , vector magnitude = “prompt weights”

# How prompting works (technical summary)

 1. There is no correct way to prompt.

2. Stable diffusion reads your prompt left to right, one token at a time, finding association _from_ the previous token _to_ the current token _and to_ the image generated thus far (Cross Attention Rule)

3. Stable Diffusion is an optimization problem that seeks to maximize similarity to prompt and minimize similarity to negatives  (Optimization Rule)

Reference material (covers entire SD , so not good source material really, but the info is there)  : https://youtu.be/sFztPP9qPRc?si=ge2Ty7wnpPGmB0gi

# The SD pipeline

For every step (20 in total by default) for SD1.5 :

1. Prompt text =>  (tokenizer)
2. => Nx768 token vectors =>(CLIP model) =>
3. 1x768 encoding => ( the SD model / Unet ) =>
4. => _Desired_ image per Rule 3 => ( sampler)
5. => Paint a section of the image => (image)

# Disclaimer /Trivia

This notebook should be seen as a "dictionary search tool"  for the vocab.json , which is the same for SD1.5 , SDXL and FLUX. Feel free to verify this by checking the 'tokenizer' folder under each model.

vocab.json in the FLUX model , for example (1 of 2 copies) : https://huggingface.co/black-forest-labs/FLUX.1-dev/tree/main/tokenizer

I'm using Clip-vit-large-patch14 , which is used in SD 1.5 , and is one among the two tokenizers for SDXL and FLUX  : https://huggingface.co/openai/clip-vit-large-patch14/blob/main/README.md

This set of tokens has dimension 1x768.  

SDXL and FLUX uses an additional set of tokens of dimension 1x1024.

These are not included in this notebook. Feel free to include them yourselves (I would appreciate that).

To do so, you will have to download a FLUX and/or SDXL model

, and copy the 49407x1024 tensor list that is stored within the model and then save it as a .pt file.

//---//

I am aware it is actually the 1x768 text_encoding being processed into an image for the SD models + FLUX.

As such , I've included text_encoding comparison at the bottom of the Notebook.

I am also aware thar SDXL and FLUX uses additional encodings , which are not included in this notebook.

* Clip-vit-bigG for SDXL: https://huggingface.co/laion/CLIP-ViT-bigG-14-laion2B-39B-b160k/blob/main/README.md

* And the T5 text encoder for FLUX. I have 0% understanding of FLUX T5 text_encoder.

//---//

If you want them , feel free to include them yourself and share the results (cuz I probably won't)  :)!

That being said , being an encoding , I reckon the CLIP Nx768 => 1x768 should be "linear" (or whatever one might call it)

So exchange a few tokens in the Nx768 for something similiar , and the resulting 1x768 ought to be kinda similar to 1x768 we had earlier. Hopefully.

I feel its important to mention this , in case some wonder why the token-token similarity don't match the text-encoding to text-encoding similarity.

# Note regarding CLIP text encoding vs. token

*To make this disclaimer clear; Token-to-token similarity is not the same as text_encoding similarity.*

I have to say this , since it will  otherwise get (even more) confusing , as both the individual tokens , and the text_encoding have dimensions 1x768.

They are separate things. Separate results. etc.

As such , you will not get anything useful if you start comparing similarity between a token , and a text-encoding. So don't do that :)!

# What about the CLIP image encoding?

The CLIP model can also do an image_encoding of an image, where the output will be a 1x768 tensor. These _can_ be compared with the text_encoding.

Comparing CLIP image_encoding with the CLIP text_encoding for a bunch of random prompts until you find the "highest similarity" , is a method used in the CLIP interrogator : https://huggingface.co/spaces/pharmapsychotic/CLIP-Interrogator

List of random prompts for CLIP interrogator  can be found here, for reference : https://github.com/pharmapsychotic/clip-interrogator/tree/main/clip_interrogator/data

The CLIP image_encoding is not included in this Notebook.

If you spot errors / ideas for improvememts; feel free to fix the code in your own notebook and post the results.

I'd appreciate that over people saying "your math is wrong you n00b!" with no constructive feedback.

//---//

Regarding output

# What are the </w> symbols?

The whitespace symbol indicate if the tokenized item ends with whitespace ( the suffix "banana</w>" => "banana " )  or not (the prefix  "post"  in "post-apocalyptic ")

For ease of reference , I call them prefix-tokens and suffix-tokens.

Sidenote:

Prefix tokens have the unique property in that they "mutate" suffix tokens

Example:  "photo of a #prefix#-banana"

where #prefix# is a randomly selected prefix-token from the vocab.json

The hyphen "-" exists to guarantee the tokenized text splits into the written #prefix# and #suffix# token respectively.  The "-" hypen symbol can be replaced by any other special character of your choosing.

 Capital letters work too , e.g "photo of a #prefix#Abanana" since the capital letters A-Z are only listed once in the entire vocab.json.

You can also choose to omit any separator and just rawdog it with the prompt "photo of a #prefix#banana" , however know that  this may , on occasion , be tokenized as completely different tokens of lower ID:s.

Curiously , common NSFW terms found online have in the CLIP model have been purposefully fragmented into separate #prefix# and #suffix# counterparts in the vocab.json. Likely for PR-reasons.

You can verify the results using this online tokenizer: https://sd-tokenizer.rocker.boo/

<div>
<img src="https://lemmy.world/pictrs/image/43467d75-7406-4a13-93ca-cdc469f944fc.jpeg" width="300"/>
<img src="https://lemmy.world/pictrs/image/c0411565-0cb3-47b1-a788-b368924d6f17.jpeg" width="300"/>
<img src="https://lemmy.world/pictrs/image/c27c6550-a88b-4543-9bd7-067dff016be2.jpeg" width="300"/>
</div>

# What is that gibberish tokens that show up?

The gibberish tokens like "ðŁĺħ\</w>" are actually emojis!

Try writing some emojis in this online tokenizer to see the results: https://sd-tokenizer.rocker.boo/

It is a bit borked as it can't process capital letters properly.

Also note that this is not reversible.

If tokenization "😅" => ðŁĺħ</w>

Then you  can't prompt "ðŁĺħ" and expect to get the same result as the tokenized original emoji , "😅".

SD 1.5 models actually have training for Emojis.

But you have to set CLIP skip to 1 for this to work is intended.

For example, this is the result from "photo of a 🧔🏻‍♂️"


<div>
<img src="https://lemmy.world/pictrs/image/e2b51aea-6960-4ad0-867e-8ce85f2bd51e.jpeg" width="300"/>
</div>

A tutorial on stuff you can do with the vocab.list concluded.

Anyways, have fun with the notebook.

There might be some updates in the future with features not mentioned here.

//---//

https://codeandlife.com/2023/01/26/mastering-the-huggingface-clip-model-how-to-extract-embeddings-and-calculate-similarity-for-text-and-images/